# Zeca Afonso

In this notebook we train a voice conversion model for Zeca Afonso.

The notebook works in three parts:
1. Preparing the training dataset
2. Training the voice conversion model
3. Inference with the voice conversion model

## 1. Preparing the training dataset

### 1.1 Extract voice from Zeca Afonso's discography

The first step is to extract the voice from the songs. We will use the [`demucs`](https://github.com/facebookresearch/demucs) Hybrid Transformer model. 

In [18]:
import subprocess
import tqdm
from pathlib import Path

for song in tqdm.tqdm(Path("../dataset/zeca/discography").rglob("*.opus")):
    command = f"demucs --two-stems=vocals \"{song}\" --out \"../dataset/zeca/discography_vocals\" --filename \"{song.stem}_{{stem}}.{{ext}}\""
    run = subprocess.run(command, shell=True, capture_output=True)

for song in tqdm.tqdm(Path("../dataset/zeca/discography").rglob("*.mp3")):
    command = f"demucs --two-stems=vocals \"{song}\" --out \"../dataset/zeca/discography_vocals\" --filename \"{song.stem}_{{stem}}.{{ext}}\""
    run = subprocess.run(command, shell=True, capture_output=True)

97it [5:11:00, 192.38s/it]
31it [1:44:48, 202.85s/it]


## 1.2 Splitting vocal files into <~ 10s duration files

To train the voice conversion model we need to split the files with voice into at small snippets of at most around 10 seconds.

First let's see how much audio we have without splitting and silence removal.

In [24]:
import librosa

duration = 0
for song in tqdm.tqdm(Path("../dataset/zeca/discography_vocals").rglob("*.wav")):
    if not "no_vocals" in song.stem:
        duration += librosa.get_duration(path=song)
print(f"Total duration: {duration} seconds / ({duration/60} minutes) / ({duration/3600} hours)")

256it [00:00, 45743.70it/s]

Total duration: 22833.76160997731 seconds / (380.56269349962184 minutes) / (6.342711558327031 hours)


Now let's use [`audio-slicer`](https://github.com/flutydeer/audio-slicer) to split the files and remove silence parts.

In [31]:
for song in tqdm.tqdm(Path("../dataset/zeca/discography_vocals").rglob("*.wav")):
    if not "no_vocals" in song.stem:
        command = f"python /home/andre/Repos/audio-slicer/slicer2.py --out ../dataset/zeca/discography_raw \"{song.absolute()}\""
        run = subprocess.run(command, shell=True, capture_output=True)

256it [02:58,  1.44it/s]


In [32]:
import librosa

durations = []
for song in tqdm.tqdm(Path("../dataset/zeca/discography_raw").rglob("*.wav")):
    if not "no_vocals" in song.stem:
        durations.append(librosa.get_duration(path=song))
duration = sum(durations)
print(f"Total duration: {duration} seconds / ({duration/60} minutes) / ({duration/3600} hours)")

print(f"Percentage of clips longer than 10 seconds: {len([d for d in durations if d > 10]) / len(durations) * 100}%")

1889it [00:00, 25705.96it/s]

Total duration: 15934.58 seconds / (265.5763333333333 minutes) / (4.426272222222222 hours)
Percentage of clips longer than 10 seconds: 19.957649550026467%


In [1]:
! cd .. && svc pre-resample

[11:48:42] INFO     [11:48:42] generated new fontManager    ]8;id=245690;file:///proj/berzelius-2023-175/users/x_andaf/so-vits-svc-fork/.venv/lib/python3.11/site-packages/matplotlib/font_manager.py\font_manager.py]8;;\:]8;id=775879;file:///proj/berzelius-2023-175/users/x_andaf/so-vits-svc-fork/.venv/lib/python3.11/site-packages/matplotlib/font_manager.py#1581\1581]8;;\
Preprocessing:  60%|█████████████▊         | 1136/1889 [00:19<00:01, 638.96it/s][11:49:11] INFO     [11:49:11] Skip                    ]8;id=577483;file:///proj/berzelius-2023-175/users/x_andaf/so-vits-svc-fork/.venv/lib/python3.11/site-packages/so_vits_svc_fork/preprocessing/preprocess_resample.py\preprocess_resample.py]8;;\:]8;id=612918;file:///proj/berzelius-2023-175/users/x_andaf/so-vits-svc-fork/.venv/lib/python3.11/site-packages/so_vits_svc_fork/preprocessing/preprocess_resample.py#71\71]8;;\
                    dataset_raw/zeca/singing/10 Canção                          
                    longe_v

In [2]:
! cd .. && svc pre-config

  0%|                                                  | 0/1888 [00:00<?, ?it/s][11:50:39] WARNING  [11:50:39]                                   ]8;id=890348;file:///software/sse/manual/Python/3.11.1/gcc-11.3.0/lib/python3.11/warnings.py\warnings.py]8;;\:]8;id=957995;file:///software/sse/manual/Python/3.11.1/gcc-11.3.0/lib/python3.11/warnings.py#109\109]8;;\
                    /proj/berzelius-2023-175/users/x_andaf/so-vi                
                    ts-svc-fork/.venv/lib/python3.11/site-packag                
                    es/so_vits_svc_fork/preprocessing/preprocess                
                    _flist_config.py:41: FutureWarning:                         
                    get_duration() keyword argument 'filename'                  
                    has been renamed to 'path' in version                       
                    0.10.0.                                                     
                            This alias will be removed in       

In [ ]:
! cd .. && svc pre-hubert

In [ ]:
! cd .. && svc train -t

[12:26:22] INFO     [12:26:22] Server binary (from Python ]8;id=619072;file:///proj/berzelius-2023-175/users/x_andaf/so-vits-svc-fork/.venv/lib/python3.11/site-packages/tensorboard/data/server_ingester.py\server_ingester.py]8;;\:]8;id=235931;file:///proj/berzelius-2023-175/users/x_andaf/so-vits-svc-fork/.venv/lib/python3.11/site-packages/tensorboard/data/server_ingester.py#290\290]8;;\
                    package v0.7.2): None                                       
[12:26:29] INFO     [12:26:29] Using strategy: auto                  ]8;id=331353;file:///proj/berzelius-2023-175/users/x_andaf/so-vits-svc-fork/.venv/lib/python3.11/site-packages/so_vits_svc_fork/train.py\train.py]8;;\:]8;id=332365;file:///proj/berzelius-2023-175/users/x_andaf/so-vits-svc-fork/.venv/lib/python3.11/site-packages/so_vits_svc_fork/train.py#98\98]8;;\
[12:26:30] WARNING  [12:26:30]                                   ]8;id=789265;file:///software/sse/manual/Python/3.11.1/gcc-11.3.0/lib/python3.11